In [1]:
#' Evaluating Gene Function Prediction
#'
#' The function performs gene function prediction based on 'guilt by association' 
#' using cross validation ([1]). Performance and significance are evaluated by 
#' calculating the AUROC or AUPRC of each functional group.
#' 
#' @param genes.labels numeric array
#' @param network numeric array symmetric, gene-by-gene matrix 
#' @param nFold numeric value, default is 3
#' @param output string, default is AUROC  
#' @param FLAG_DRAW binary flag to draw roc plot
#'
#' @return scores numeric matrix with a row for each gene label and columns
#'         auc: the average area under the ROC or PR curve for the neighbor voting predictor
#'              across cross validation replicates
#'         avg_node_degree: the average node degree
#'         degree_null_auc: the area the ROC or PR curve for the node degree predictor
#' 
#' @keywords neighbor voting 
#' guilt by association 
#' gene function prediction evaluation 
#' cross validation
#'
#' @examples 
#' genes.labels <- matrix( sample( c(0,1), 1000, replace=TRUE), nrow=100)
#' rownames(genes.labels) = paste('gene', 1:100, sep='')
#' colnames(genes.labels) = paste('function', 1:10, sep='')
#' net <- cor( matrix( rnorm(10000), ncol=100), method='spearman')
#' rownames(net) <- paste('gene', 1:100, sep='')
#' colnames(net) <- paste('gene', 1:100, sep='')
#' 
#' aurocs <- neighbor_voting(genes.labels, net, output = 'AUROC') 
#' 
#' avgprcs <- neighbor_voting(genes.labels, net, output = 'PR') 
#' 
#' @export
#'
#'  
neighbor_voting <- function(genes.labels, network, nFold = 3, output = "AUROC", FLAG_DRAW = FALSE) {

    genes.labels <- as.matrix(genes.labels);
    # Filter for common genes between network and labels
    #ord <- order(rownames(network));
    #network <- network[ord, ord];
    #ord <- order(rownames(genes.labels));
    #genes.labels <- as.matrix(genes.labels[ord, ]);


    maskNet <- rownames(network) %in% rownames(genes.labels)
    network <- network[maskNet,maskNet]

    maskLab <- match(rownames(network),rownames(genes.labels))
    genes.labels <- as.matrix(genes.labels[maskLab, ]);
    #match.lab <- match(rownames(genes.labels), rownames(network));
    #filt.lab <- !is.na(match.lab);
    #filt.net <- match.lab[filt.lab];

    #network <- network[filt.net, filt.net]

    #genes.labels <- as.matrix(genes.labels[filt.lab, ]);
    # genes.label : needs to be in 1s and 0s
    l <- dim(genes.labels)[2];
    g <- dim(genes.labels)[1];
    ab <- which(genes.labels != 0, arr.ind = TRUE);
    n <- length(ab[, 1]);
    
    # print('Make genes label CV matrix')
    if (!require('Matrix', quietly=TRUE)) {
        install.packages('Matrix')
        library(Matrix)
    }
    
    test.genes.labels <- matrix(genes.labels, nrow = g, ncol = nFold * l)
    test.genes.labels <- as(test.genes.labels,'sparseMatrix')

    # For each fold in each GO group, remove 1/nth of the values of the genes.label
    for (j in 1:l) {
        d <- which(ab[, 2] == j)  # Which indices the genes are in this particular GO group
        t <- length(d)  # Total number of genes in the GO group
        r <- sample(1:t, replace = FALSE)
        f <- t/nFold
        for (i in 1:nFold) {
            e <- c((1:f) + f * (i - 1))
            e <- sort(r[e])
            c <- j + l * (i - 1)  # GO group to look at (ie column)
            test.genes.labels[ab[d], c][e] <- 0
        }
    }

    # print('Get sums - mat. mul.') sumin = ( t(network) %*% test.genes.labels) sumin <- ((network)
    # %*% test.genes.labels)
    sumin <- crossprod(network, test.genes.labels)

    # print('Get sums - calc sumall')
    sumall <- matrix(colSums(network), ncol = dim(sumin)[2], nrow = dim(sumin)[1])

    # print('Get sums - calc predicts')
    predicts <- sumin/sumall
    
    
    if (output == "AUROC") {
        # print('Hide training data')
        nans <- which(test.genes.labels == 1, arr.ind = TRUE)

        predicts[nans] <- NA

        if (!require('foreach', quietly=TRUE)) {
           install.packages('foreach')
           library(foreach)
           library(iterators)
        }
        library(iterators)
        predicts <- as.matrix(predicts)
        #print('Rank test data')
        predicts <- foreach(predicts=iter(predicts,by='col'),.combine=cbind) %dopar% (rank(abs(predicts),na.last = "keep", ties.method = "average"))

        # if (!require('parallel', quietly=TRUE)) {
        # install.packages('parallel')
        # library(parallel)
        # }
        # predicts <- as.matrix(predicts)
        # clust <- makeCluster(detectCores())
        # predicts <- parSapply(clust, predicts <- iter(predicts,by='col'), function(x) rank(abs(x),na.last = "keep", ties.method = "average"))
        # stopCluster(clust)

        filter <- matrix(genes.labels, nrow = g, ncol = nFold * l)
        negatives <- which(filter == 0, arr.ind = TRUE)
        positives <- which(filter == 1, arr.ind = TRUE)

        predicts[negatives] <- 0
        temp1 <- colSums(test.genes.labels)
        temp2 <- colSums(filter)

        # print('Calculate ROC - np')
        #np <- colSums(filter) - colSums(test.genes.labels)  # Postives
        np <- temp2-temp1

        # print('Calculate ROC - nn')
        #nn <- dim(test.genes.labels)[1] - colSums(filter)  # Negatives
        nn <- dim(test.genes.labels)[1] - temp2

        # print('Calculate ROC - p')
        p <- apply(predicts, 2, sum, na.rm = TRUE)

        # print('Calculate ROC - rocN')
        rocN <- (p/np - (np + 1)/2)/nn
        rocN <- matrix(rocN, ncol = nFold, nrow = l)
        rocN <- rowMeans(rocN)

        # print('Calculate node degree')
        node_degree <- rowSums(network)
        colsums <- colSums(genes.labels)

        # print('Calculate node degree - sum across gene labels')
        node_degree <- matrix(node_degree)
        temp <- t(node_degree) %*% genes.labels

        # print('Calculate node degree - average')
        average_node_degree <- t(temp)/colsums

        # print('Calculate node degree roc - rank node degree')
        ranks <- apply(abs(node_degree), 2, rank, na.last = "keep", ties.method = "average")
        ranks <- matrix(ranks, nrow = length(ranks), ncol = dim(genes.labels)[2])

        # print('Calculate node degree roc - remove negatives')
        negatives <- which(genes.labels == 0, arr.ind = TRUE)
        ranks[negatives] <- 0

        # print('Calculate node degree roc - np')
        np <- colSums(genes.labels)

        # print('Calculate node degree roc - nn')
        nn <- dim(genes.labels)[1] - np

        # print('Calculate node degree roc - p')
        p <- apply(ranks, 2, sum, na.rm = TRUE)

        # print('Calculate node degree roc - roc')
        roc <- (p/np - (np + 1)/2)/nn
        
        if (FLAG_DRAW == TRUE) {
            plot_roc_overlay(predicts, test.genes.labels)
        }
        
        scores <- cbind(
            auc=rocN,
            avg_node_degree=matrix(average_node_degree)[, 1],
            degree_null_auc=roc)
    } else if (output == "PR") {
        
    	nans <- which(test.genes.labels == 1, arr.ind = TRUE)
        predicts[nans] <- NA
        filter <- matrix(genes.labels, nrow = g, ncol = nFold * l)
        negatives <- which(filter == 0, arr.ind = TRUE)
        positives <- which(filter == 1, arr.ind = TRUE)

        # print('Rank test data')
        if (!require('foreach', quietly=TRUE)) {
           install.packages('foreach')
           library(foreach)
        }
        library(iterators)
        predicts <- as.matrix(predicts)
        #print('Rank test data')
        predicts <- foreach(predicts=iter(predicts,by='col'),.combine=cbind) %dopar% (rank(-abs(predicts),na.last = "keep", ties.method = "average"))
        predicts[negatives] <- 0

        avgprc.s <- lapply(1:(nFold * l), function(i)  
                  mean(  ( 1:length(which( sort(predicts[,i]) > 0   )  )
                        / sort(predicts[,i])[ which( sort(predicts[,i]) > 0 )]), na.rm = TRUE)   )
 
        n.s <- colSums(test.genes.labels)
        avgprc.null <- lapply(1:(nFold * l), function(i) n.s[i]/g)
        avgprc.null <- rowMeans(matrix(unlist(avgprc.null), ncol = nFold, nrow = l, byrow = FALSE), 
               na.rm = TRUE)

        avgprc <- rowMeans(matrix(unlist(avgprc.s), ncol = nFold, nrow = l, byrow = FALSE), na.rm = TRUE)
        names(avgprc) <- colnames(genes.labels)
        
        # print('Calculate node degree')
        node_degree <- rowSums(network)
        colsums <- colSums(genes.labels)
        
        # print('Calculate node degree - sum across gene labels')
        node_degree <- matrix(node_degree)
        temp <- t(node_degree) %*% genes.labels
        
        
        # print('Calculate node degree - average')
        average_node_degree <- t(temp)/colsums
        
        scores <- cbind(
            avgprc=avgprc,
            avg_node_degree=matrix(average_node_degree)[, 1],
            degree_null_auc=avgprc.null)
    }


    return(scores)
}

In [3]:
genes.labels <- matrix( sample( c(0,1), 1000, replace=TRUE), nrow=100)
rownames(genes.labels) = paste('gene', 1:100, sep='')
colnames(genes.labels) = paste('function', 1:10, sep='')
net <- cor( matrix( rnorm(10000), ncol=100), method='spearman')
rownames(net) <- paste('gene', 1:100, sep='')
colnames(net) <- paste('gene', 1:100, sep='')

aurocs <- neighbor_voting(genes.labels, net, output = 'AUROC') 

avgprcs <- neighbor_voting(genes.labels, net, output = 'PR') 

Warning message:
“executing %dopar% sequentially: no parallel backend registered”


In [41]:
file_path <- "/grid/gillis/home/lohia/notebooks_cre_v3/notebooks/Notebooks_clean/input_go1.csv"

# Read the CSV file into a data frame with row names and headers
data_frame <- read.csv(file_path, header = TRUE, row.names = 1)

# Get the row names and column names from the data frame
row_names <- rownames(data_frame)
col_names <- colnames(data_frame)

genes.labels <- as.matrix(data_frame)

In [35]:
genes.labels

CGE.derived MGE.derived Glut Gaba CGE.derived.1
Chandelier               1           0           0    1    1            
Lamp5                    0           1           0    1    0            
Lamp5_Lhx6               0           1           0    1    0            
Pax6                     0           1           0    1    0            
Pvalb                    1           0           0    1    1            
Sncg                     0           1           0    1    0            
Sst                      1           0           0    1    1            
Sst Chodl                1           0           0    1    1            
Vip                      0           1           0    1    0            
L2/3 IT                  0           0           1    0    0            
L4 IT                    0           0           1    0    0            
L5 ET                    0           0           1    0    0            
L5 IT                    0           0           1    0    0            
L5/6 NP                  0           0           1    0    0            
L6 CT                    0           0           1    0    0            
L6 IT                    0           0           1    0    0            
L6 IT Car3               0           0           1    0    0            
L6b                      0           0           1    0    0            
Astro                    0           0           0    0    0            
Endo                     0           0           0    0    0            
Micro-PVM                0           0           0    0    0            
OPC                      0           0           0    0    0            
Oligo                    0           0           0    0    0            
VLMC                     0           0           0    0    0            
Adipocytes               0           0           0    0    0            
Cardiomyocytes           0           0           0    0    0            
Endocardial              0           0           0    0    0            
Endothelial_Arterial     0           0           0    0    0            
Endothelial_Capillaries  0           0           0    0    0            
Endothelial_Other        0           0           0    0    0            
Endothelial_Venous       0           0           0    0    0            
Epicardium_FB-like       0           0           0    0    0            
Epicardium_Meso          0           0           0    0    0            
Epicardium_Proliferating 0           0           0    0    0            
Fibroblasts              0           0           0    0    0            
Immature_Cardiomyocytes  0           0           0    0    0            
Immature_other           0           0           0    0    0            
Lymphoid_Immune_Cells    0           0           0    0    0            
Myeloid_Immune_Cells     0           0           0    0    0            
Neuronal_Cells           0           0           0    0    0            
Pericytes                0           0           0    0    0            
Pericytes_Stromal        0           0           0    0    0            
Smooth_Muscle_Cells      0           0           0    0    0            
                         MGE.derived.1
Chandelier               0            
Lamp5                    1            
Lamp5_Lhx6               1            
Pax6                     1            
Pvalb                    0            
Sncg                     1            
Sst                      0            
Sst Chodl                0            
Vip                      1            
L2/3 IT                  0            
L4 IT                    0            
L5 ET                    0            
L5 IT                    0            
L5/6 NP                  0            
L6 CT                    0            
L6 IT                    0            
L6 IT Car3               0            
L6b                      0            
Astro                    0            
Endo                     0       

In [25]:
file_path <- "/grid/gillis/home/lohia/notebooks_cre_v3/notebooks/Notebooks_clean/input_nw.csv"

# Read the CSV file into a data frame with row names and headers
data_frame <- read.csv(file_path, header = TRUE, row.names = 1)

# Get the row names and column names from the data frame
row_names <- colnames(data_frame)
col_names <- colnames(data_frame)

net <- as.matrix(data_frame)

In [26]:
net

Chandelier Lamp5      Lamp5_Lhx6 Pax6       Pvalb     
Chandelier               1.20330758 0.15968528 0.15291785 0.04511277 0.16325579
Lamp5                    0.15968528 1.20330758 0.12925042 0.16790264 0.19095669
Lamp5_Lhx6               0.15291785 0.12925042 1.20330758 0.19073092 0.21196927
Pax6                     0.04511277 0.16790264 0.19073092 1.20330758 0.22717899
Pvalb                    0.16325579 0.19095669 0.21196927 0.22717899 1.20330758
Sncg                     0.24261659 0.20377969 0.14034849 0.24349619 0.23352632
Sst                      0.21584432 0.19572606 0.29890308 0.21270595 0.17459137
Sst Chodl                0.19318252 0.08471194 0.19568027 0.22160009 0.14099836
Vip                      0.17398419 0.22959104 0.19690524 0.16988884 0.14990011
L2/3 IT                  0.16669807 0.21480699 0.14493024 0.19401265 0.22669809
L4 IT                    0.16471637 0.25250309 0.06892663 0.13671572 0.18474821
L5 ET                    0.20706568 0.19360176 0.14415534 0.11856450 0.18346170
L5 IT                    0.16242333 0.13732842 0.18082827 0.17326712 0.19442305
L5/6 NP                  0.17682510 0.17168430 0.22210132 0.30272253 0.23861505
L6 CT                    0.13674189 0.12445942 0.20063602 0.09033107 0.07238937
L6 IT                    0.15723506 0.21127879 0.19373085 0.19833235 0.26868143
L6 IT Car3               0.16696287 0.06945630 0.27214279 0.16986778 0.24244700
L6b                      0.16076999 0.16652822 0.25181404 0.15602638 0.19402899
Astro                    0.21103566 0.23385411 0.06529184 0.19650894 0.17522762
Endo                     0.19715339 0.13071821 0.18689669 0.11735937 0.14584475
Micro-PVM                0.12833390 0.22015716 0.12793123 0.20954085 0.11918398
OPC                      0.15919948 0.35345536 0.16465469 0.17394019 0.27343947
Oligo                    0.28365681 0.11103242 0.16378144 0.06238968 0.12439020
VLMC                     0.23259636 0.16106132 0.15825326 0.18058031 0.11391497
Adipocytes               0.21670994 0.18346602 0.07606254 0.14097467 0.15001698
Cardiomyocytes           0.17335877 0.15476226 0.09958796 0.22887772 0.16861021
Endocardial              0.16024788 0.20276349 0.05084134 0.14585696 0.12665514
Endothelial_Arterial     0.15654861 0.16912202 0.25763202 0.11680439 0.22219058
Endothelial_Capillaries  0.16368928 0.16874333 0.05259819 0.14215234 0.14549787
Endothelial_Other        0.23010475 0.11513313 0.14970971 0.13964463 0.14642737
Endothelial_Venous       0.17860894 0.14409890 0.20882043 0.22001873 0.10450804
Epicardium_FB-like       0.26054145 0.10627146 0.17071464 0.21355322 0.24676904
Epicardium_Meso          0.20055905 0.20688971 0.08964945 0.12836272 0.13970729
Epicardium_Proliferating 0.17705891 0.28933458 0.19040096 0.08437040 0.13807528
Fibroblasts              0.10388116 0.19633043 0.32141370 0.26874698 0.19084103
Immature_Cardiomyocytes  0.14178679 0.02398655 0.19988495 0.24246184 0.15769260
Immature_other           0.17649877 0.10245610 0.20195581 0.12646193 0.18233546
Lymphoid_Immune_Cells    0.18082553 0.15050198 0.23337046 0.16021723 0.22590904
Myeloid_Immune_Cells     0.20842159 0.09280053 0.12985490 0.23728794 0.07366606
Neuronal_Cells           0.17587669 0.24086813 0.25250128 0.14040530 0.18589063
Pericytes                0.13048658 0.14959718 0.14266107 0.26136330 0.19715391
Pericytes_Stromal        0.14199307 0.14934393 0.17350379 0.20663196 0.17115453
Smooth_Muscle_Cells      0.23997149 0.15382051 0.17849828 0.18134501 0.19725048
                         Sncg       Sst        Sst.Chodl  Vip        L2.3.IT   
Chandelier               0.24261659 0.21584432 0.19318252 0.17398419 0.16669807
Lamp5                    0.20377969 0.19572606 0.08471194 0.22959104 0.21480699
Lamp5_Lhx6               0.14034849 0.29890308 0.19568027 0.19690524 0.14493024
Pax6                     0.24349619 0.21270595 0.22160009 0.16988884 0.19401265
Pvalb                    0.23352632 0.17459137 0.14099836 0.14990011 0.22669809
Sncg                     

In [42]:
aurocs <- neighbor_voting(genes.labels, net, output = 'AUROC') 

avgprcs <- neighbor_voting(genes.labels, net, output = 'PR') 

In [43]:
aurocs

auc       avg_node_degree degree_null_auc
CGE.derived 0.4188034 8.632025        0.6282051      
MGE.derived 0.5701754 8.468405        0.3578947      
Glut        0.8725490 8.493600        0.3986928      
Gaba        0.5065359 8.541125        0.4771242

In [19]:
aurocs

auc       avg_node_degree degree_null_auc
brain 0.8421053 8.558820        0.4868421      
heart 0.8217593 8.608051        0.5131579      
Gaba  0.6013072 8.541125        0.4771242

In [33]:
aurocs

auc       avg_node_degree degree_null_auc
brain 0.8092105 8.558820        0.4868421      
heart 0.8263889 8.608051        0.5131579      
Gaba  0.6176471 8.541125        0.4771242      
Glut  0.9019608 8.493600        0.3986928